In [ ]:
# Run below commands in google colab
# install Java8
!apt-get update --fix-missing

!apt-get install openjdk-8-jdk-headless -qq > /dev/null

# download spark3.0.0
!wget -q https://archive.apache.org/dist/spark/spark-3.0.0/spark-3.0.0-bin-hadoop3.2.tgz

Get:1 http://security.ubuntu.com/ubuntu bionic-security InRelease [88.7 kB]
Get:2 https://cloud.r-project.org/bin/linux/ubuntu bionic-cran40/ InRelease [3,626 B]
Ign:3 https://developer.download.nvidia.com/compute/machine-learning/repos/ubuntu1804/x86_64  InRelease
Hit:4 http://ppa.launchpad.net/c2d4u.team/c2d4u4.0+/ubuntu bionic InRelease
Hit:5 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu1804/x86_64  InRelease
Hit:6 https://developer.download.nvidia.com/compute/machine-learning/repos/ubuntu1804/x86_64  Release
Hit:7 http://archive.ubuntu.com/ubuntu bionic InRelease
Get:8 http://archive.ubuntu.com/ubuntu bionic-updates InRelease [88.7 kB]
Hit:9 http://ppa.launchpad.net/cran/libgit2/ubuntu bionic InRelease
Hit:10 http://ppa.launchpad.net/deadsnakes/ppa/ubuntu bionic InRelease
Get:11 http://archive.ubuntu.com/ubuntu bionic-backports InRelease [74.6 kB]
Get:12 http://security.ubuntu.com/ubuntu bionic-security/main amd64 Packages [2,965 kB]
Hit:13 http://ppa.launchpad.ne

In [ ]:
# unzip the spark file
!tar xf spark-3.0.0-bin-hadoop3.2.tgz

# install findspark 
!pip install -q findspark

In [ ]:
# set environmental variables
import os
os.environ["JAVA_HOME"] = "/usr/lib/jvm/java-8-openjdk-amd64"
os.environ["SPARK_HOME"] = "/content/spark-3.0.0-bin-hadoop3.2"

In [ ]:
import findspark
findspark.init()

In [ ]:
from pyspark.sql import SparkSession

spark = ( SparkSession.builder
                      .master("local[*]")
                      #.config("spark.sql.warehouse.dir", "./")
                      #.config("spark.some.config.option", "some-value")
                      .getOrCreate() 
                      )

sc = spark.sparkContext #spark context

In [ ]:
# spark version
sc.version

'3.0.0'

In [ ]:
df_1000records_data= ( spark.read
                              .load("/content/npi___1000_records.csv",
                                    format = 'csv',
                                    sep=",", 
                                    #schema = schema, #you can specify schema explicitly
                                    inferSchema="true", #you can try to infer schema
                                    header="true")
)

#check the first rows
df_1000records_data.show()

+----------+----------------+---------------+------------------------------------+------------------------------------------------+-------------------------------+-------------------+--------------------+-------------------------+-------------------------+------------------------+--------------------------------+------------------------------------------+------------------------+-------------------------+--------------------------+-------------------------------+-------------------------------+------------------------------+----------------------------------+--------------------------------------------+---------------------------------------------+-------------------------------------------+--------------------------------------------+---------------------------------------------+----------------------------------------------------------------+--------------------------------------------------+--------------------------------------------+------------------------------------------------

In [ ]:
df_deactivated_data= ( spark.read
                              .load("/content/NPPES-Deactivated-NPI-Report-20220809.csv",
                                    format = 'csv',
                                    sep=",", 
                                    #schema = schema, #you can specify schema explicit
                                     header="true" )
)

#check the first rows
df_deactivated_data.show()

+----------+-----------------------+
|       NPI|NPPES Deactivation Date|
+----------+-----------------------+
|1700455433|             08-09-2022|
|1841956893|             08-08-2022|
|1821755646|             08-08-2022|
|1407160179|             08-08-2022|
|1780796912|             08-08-2022|
|1568507937|             08-08-2022|
|1891148748|             08-08-2022|
|1730532680|             08-08-2022|
|1144335696|             08-08-2022|
|1487033908|             08-08-2022|
|1508288366|             08-08-2022|
|1013503119|             08-08-2022|
|1548897531|             08-08-2022|
|1932154879|             08-08-2022|
|1225760218|             08-08-2022|
|1821208380|             08-08-2022|
|1134504533|             08-08-2022|
|1932679305|             08-08-2022|
|1144638347|             08-08-2022|
|1326455627|             08-08-2022|
+----------+-----------------------+
only showing top 20 rows



In [ ]:
df=df_1000records_data.join(df_deactivated_data,on = ['NPI'],how="left_anti")
df.show()#REMOVING THE DEACTIVATED CUSTOMERS

+----------+----------------+---------------+------------------------------------+------------------------------------------------+-------------------------------+-------------------+--------------------+-------------------------+-------------------------+------------------------+--------------------------------+------------------------------------------+------------------------+-------------------------+--------------------------+-------------------------------+-------------------------------+------------------------------+----------------------------------+--------------------------------------------+---------------------------------------------+-------------------------------------------+--------------------------------------------+---------------------------------------------+----------------------------------------------------------------+--------------------------------------------------+--------------------------------------------+------------------------------------------------

In [ ]:
df_incremental_data = ( spark.read
                              .load("/content/incremental_weekly_data.csv",
                                    format = 'csv',
                                    sep=",", 
                                    #schema = schema, #you can specify schema explicit
                                     header="true" )
)
#check the first rows
df_incremental_data.show()


+----------+----------------+---------------+------------------------------------+------------------------------------------------+-------------------------------+-------------------+--------------------+-------------------------+-------------------------+------------------------+--------------------------------+------------------------------------------+------------------------+-------------------------+--------------------------+-------------------------------+-------------------------------+------------------------------+----------------------------------+--------------------------------------------+---------------------------------------------+-------------------------------------------+--------------------------------------------+---------------------------------------------+----------------------------------------------------------------+--------------------------------------------------+--------------------------------------------+------------------------------------------------

In [ ]:
df2=df.union(df_incremental_data)
df2.show()#ADDING NEW WEEKLY CUSTOMERS

+----------+----------------+---------------+------------------------------------+------------------------------------------------+-------------------------------+-------------------+--------------------+-------------------------+-------------------------+------------------------+--------------------------------+------------------------------------------+------------------------+-------------------------+--------------------------+-------------------------------+-------------------------------+------------------------------+----------------------------------+--------------------------------------------+---------------------------------------------+-------------------------------------------+--------------------------------------------+---------------------------------------------+----------------------------------------------------------------+--------------------------------------------------+--------------------------------------------+------------------------------------------------

ENTITY TYPE CODE

In [ ]:
from pyspark.sql.functions import regexp_replace
df2=df2.withColumn('Entity Type Code', regexp_replace('Entity Type Code', '1', '1, Individual')) \
   .withColumn('Entity Type Code', regexp_replace('Entity Type Code', '2', '2, Organization'))

In [ ]:
df2.show()

+----------+----------------+---------------+------------------------------------+------------------------------------------------+-------------------------------+-------------------+--------------------+-------------------------+-------------------------+------------------------+--------------------------------+------------------------------------------+------------------------+-------------------------+--------------------------+-------------------------------+-------------------------------+------------------------------+----------------------------------+--------------------------------------------+---------------------------------------------+-------------------------------------------+--------------------------------------------+---------------------------------------------+----------------------------------------------------------------+--------------------------------------------------+--------------------------------------------+------------------------------------------------

Sole Proprietor Codes

In [ ]:
# Sole Proprietor Codes 
df3=df2.withColumn('Is Sole Proprietor', regexp_replace('Is Sole Proprietor', 'X', 'X, Not Answered')) \
        .withColumn('Is Sole Proprietor', regexp_replace('Is Sole Proprietor', 'Y', 'Y, Yes')) \
        .withColumn('Is Sole Proprietor', regexp_replace('Is Sole Proprietor', 'N', 'N, No')) 
df3.show()


+----------+----------------+---------------+------------------------------------+------------------------------------------------+-------------------------------+-------------------+--------------------+-------------------------+-------------------------+------------------------+--------------------------------+------------------------------------------+------------------------+-------------------------+--------------------------+-------------------------------+-------------------------------+------------------------------+----------------------------------+--------------------------------------------+---------------------------------------------+-------------------------------------------+--------------------------------------------+---------------------------------------------+----------------------------------------------------------------+--------------------------------------------------+--------------------------------------------+------------------------------------------------

 Subpart Codes

In [ ]:
# Subpart_Codes
df4=df3.withColumn('Is Organization Subpart', regexp_replace('Is Organization Subpart', 'X', 'X, Not Answered')) \
         .withColumn('Is Organization Subpart', regexp_replace('Is Organization Subpart', 'Y', 'Y, Yes')) \
         .withColumn('Is Organization Subpart', regexp_replace('Is Organization Subpart', 'N', 'N, No')) 
df4.show()


+----------+----------------+---------------+------------------------------------+------------------------------------------------+-------------------------------+-------------------+--------------------+-------------------------+-------------------------+------------------------+--------------------------------+------------------------------------------+------------------------+-------------------------+--------------------------+-------------------------------+-------------------------------+------------------------------+----------------------------------+--------------------------------------------+---------------------------------------------+-------------------------------------------+--------------------------------------------+---------------------------------------------+----------------------------------------------------------------+--------------------------------------------------+--------------------------------------------+------------------------------------------------

Gender Codes

In [ ]:
# Gender Codes
df5=df4.withColumn('Provider Gender Code', regexp_replace('Provider Gender Code', 'M', 'M, Male')) \
         .withColumn('Provider Gender Code', regexp_replace('Provider Gender Code', 'F', 'F, Female')) 
df5.show()   

+----------+----------------+---------------+------------------------------------+------------------------------------------------+-------------------------------+-------------------+--------------------+-------------------------+-------------------------+------------------------+--------------------------------+------------------------------------------+------------------------+-------------------------+--------------------------+-------------------------------+-------------------------------+------------------------------+----------------------------------+--------------------------------------------+---------------------------------------------+-------------------------------------------+--------------------------------------------+---------------------------------------------+----------------------------------------------------------------+--------------------------------------------------+--------------------------------------------+------------------------------------------------

Deactivation Reason Codes 

In [ ]:

df6=df5.withColumn('NPI Deactivation Reason Code', regexp_replace('NPI Deactivation Reason Code', 'DT', 'DT, Death')) \
         .withColumn('NPI Deactivation Reason Code', regexp_replace('NPI Deactivation Reason Code', 'DB', 'DB, Disbandment')) \
         .withColumn('NPI Deactivation Reason Code', regexp_replace('NPI Deactivation Reason Code', 'FR', 'FR, Fraud')) \
         .withColumn('NPI Deactivation Reason Code', regexp_replace('NPI Deactivation Reason Code', 'OT', 'OT, Other')) 
df6.show()  

+----------+----------------+---------------+------------------------------------+------------------------------------------------+-------------------------------+-------------------+--------------------+-------------------------+-------------------------+------------------------+--------------------------------+------------------------------------------+------------------------+-------------------------+--------------------------+-------------------------------+-------------------------------+------------------------------+----------------------------------+--------------------------------------------+---------------------------------------------+-------------------------------------------+--------------------------------------------+---------------------------------------------+----------------------------------------------------------------+--------------------------------------------------+--------------------------------------------+------------------------------------------------

Deactivation Reason Codes 

In [ ]:
df7=df6.withColumn('NPI Deactivation Reason Code', regexp_replace('NPI Deactivation Reason Code', 'DT', 'DT, Death')) \
         .withColumn('NPI Deactivation Reason Code', regexp_replace('NPI Deactivation Reason Code', 'DB', 'DB, Disbandment')) \
         .withColumn('NPI Deactivation Reason Code', regexp_replace('NPI Deactivation Reason Code', 'FR', 'FR, Fraud')) \
         .withColumn('NPI Deactivation Reason Code', regexp_replace('NPI Deactivation Reason Code', 'OT', 'OT, Other')) 
df7.show()         


+----------+----------------+---------------+------------------------------------+------------------------------------------------+-------------------------------+-------------------+--------------------+-------------------------+-------------------------+------------------------+--------------------------------+------------------------------------------+------------------------+-------------------------+--------------------------+-------------------------------+-------------------------------+------------------------------+----------------------------------+--------------------------------------------+---------------------------------------------+-------------------------------------------+--------------------------------------------+---------------------------------------------+----------------------------------------------------------------+--------------------------------------------------+--------------------------------------------+------------------------------------------------

 Other Provider Name Type Codes

In [ ]:
df8=df7.withColumn('Provider Other Organization Name Type Code', regexp_replace('Provider Other Organization Name Type Code', '1', '1, Former Name, I')) \
         .withColumn('Provider Other Organization Name Type Code', regexp_replace('Provider Other Organization Name Type Code', '2', '2, Professional Name, I')) \
         .withColumn('Provider Other Organization Name Type Code', regexp_replace('Provider Other Organization Name Type Code', '3', '3, Doing Business As, O')) \
         .withColumn('Provider Other Organization Name Type Code', regexp_replace('Provider Other Organization Name Type Code', '4', '4, Former Legal Business Name, O')) \
         .withColumn('Provider Other Organization Name Type Code', regexp_replace('Provider Other Organization Name Type Code', '5', '5, Other Name, B')) 
df8.show()       

+----------+----------------+---------------+------------------------------------+------------------------------------------------+-------------------------------+-------------------+--------------------+-------------------------+-------------------------+------------------------+--------------------------------+------------------------------------------+------------------------+-------------------------+--------------------------+-------------------------------+-------------------------------+------------------------------+----------------------------------+--------------------------------------------+---------------------------------------------+-------------------------------------------+--------------------------------------------+---------------------------------------------+----------------------------------------------------------------+--------------------------------------------------+--------------------------------------------+------------------------------------------------

 Provider Name Prefix Codes

In [ ]:
df9=df8.withColumn('Provider Other Last Name Type Code', regexp_replace('Provider Other Last Name Type Code', '1', '1, Former Name, I')) \
         .withColumn('Provider Other Last Name Type Code', regexp_replace('Provider Other Last Name Type Code', '2', '2, Professional Name, I')) \
         .withColumn('Provider Other Last Name Type Code', regexp_replace('Provider Other Last Name Type Code', '3', '3, Doing Business As, O')) \
         .withColumn('Provider Other Last Name Type Code', regexp_replace('Provider Other Last Name Type Code', '4', '4, Former Legal Business Name, O')) \
         .withColumn('Provider Other Last Name Type Code', regexp_replace('Provider Other Last Name Type Code', '5', '5, Other Name, B')) 
df9.show()      

+----------+----------------+---------------+------------------------------------+------------------------------------------------+-------------------------------+-------------------+--------------------+-------------------------+-------------------------+------------------------+--------------------------------+------------------------------------------+------------------------+-------------------------+--------------------------+-------------------------------+-------------------------------+------------------------------+----------------------------------+--------------------------------------------+---------------------------------------------+-------------------------------------------+--------------------------------------------+---------------------------------------------+----------------------------------------------------------------+--------------------------------------------------+--------------------------------------------+------------------------------------------------

 Provider Name Prefix Codes


In [ ]:
df_provider_suffix=df9.withColumn('Provider Name Prefix Text', regexp_replace('Provider Name Prefix Text', 'MS.', 'MS., MS.')) \
         .withColumn('Provider Name Prefix Text', regexp_replace('Provider Name Prefix Text', 'MR', 'Mr., Mr.')) \
         .withColumn('Provider Name Prefix Text', regexp_replace('Provider Name Prefix Text', 'MiSS', 'MiSS, MISS')) \
         .withColumn('Provider Name Prefix Text', regexp_replace('Provider Name Prefix Text', 'DR.', 'DR., DR.')) \
         .withColumn('Provider Name Prefix Text', regexp_replace('Provider Name Prefix Text', 'PROF.', 'PROF., PROF.')) 
df_provider_suffix.show(100)       



+----------+----------------+---------------+------------------------------------+------------------------------------------------+-------------------------------+-------------------+--------------------+-------------------------+-------------------------+------------------------+--------------------------------+------------------------------------------+------------------------+-------------------------+--------------------------+-------------------------------+-------------------------------+------------------------------+----------------------------------+--------------------------------------------+---------------------------------------------+-------------------------------------------+--------------------------------------------+---------------------------------------------+----------------------------------------------------------------+--------------------------------------------------+--------------------------------------------+------------------------------------------------

In [ ]:
df11=df_provider_suffix.withColumn('Authorized Official Name Prefix Text', regexp_replace('Authorized Official Name Prefix Text', 'MS.', 'MS., MS.')) \
         .withColumn('Authorized Official Name Prefix Text', regexp_replace('Authorized Official Name Prefix Text', 'MR', 'MR., MR.')) \
         .withColumn('Authorized Official Name Prefix Text', regexp_replace('Authorized Official Name Prefix Text', 'Miss', 'Miss, Miss')) \
         .withColumn('Authorized Official Name Prefix Text', regexp_replace('Authorized Official Name Prefix Text', 'DR.', 'DR., DR.')) \
         .withColumn('Authorized Official Name Prefix Text', regexp_replace('Authorized Official Name Prefix Text', 'PROF.', 'PROF., PROF.')) 
df11.show()        

+----------+----------------+---------------+------------------------------------+------------------------------------------------+-------------------------------+-------------------+--------------------+-------------------------+-------------------------+------------------------+--------------------------------+------------------------------------------+------------------------+-------------------------+--------------------------+-------------------------------+-------------------------------+------------------------------+----------------------------------+--------------------------------------------+---------------------------------------------+-------------------------------------------+--------------------------------------------+---------------------------------------------+----------------------------------------------------------------+--------------------------------------------------+--------------------------------------------+------------------------------------------------

In [ ]:
df12=df11.withColumn('Authorized Official Name Prefix Text', regexp_replace('Authorized Official Name Prefix Text', 'MS.', 'MS., MS.')) \
         .withColumn('Authorized Official Name Prefix Text', regexp_replace('Authorized Official Name Prefix Text', 'MR', 'MR., MR.')) \
         .withColumn('Authorized Official Name Prefix Text', regexp_replace('Authorized Official Name Prefix Text', 'MISS', 'MISS, MISS')) \
         .withColumn('Authorized Official Name Prefix Text', regexp_replace('Authorized Official Name Prefix Text', 'DR.', 'DR., DR.')) \
         .withColumn('Authorized Official Name Prefix Text', regexp_replace('Authorized Official Name Prefix Text', 'PROF.', 'PROF., PROF.')) 
df12.show()        

+----------+----------------+---------------+------------------------------------+------------------------------------------------+-------------------------------+-------------------+--------------------+-------------------------+-------------------------+------------------------+--------------------------------+------------------------------------------+------------------------+-------------------------+--------------------------+-------------------------------+-------------------------------+------------------------------+----------------------------------+--------------------------------------------+---------------------------------------------+-------------------------------------------+--------------------------------------------+---------------------------------------------+----------------------------------------------------------------+--------------------------------------------------+--------------------------------------------+------------------------------------------------

 Name suffix Codes

In [ ]:

df13=df12.withColumn('Provider Name Suffix Text', regexp_replace('Provider Name Suffix Text', 'Jr.', 'Jr., Jr')) \
          .withColumn('Provider Name Suffix Text', regexp_replace('Provider Name Suffix Text', 'Sr.', 'Sr., Sr.')) \
          .withColumn('Provider Name Suffix Text', regexp_replace('Provider Name Suffix Text', 'I', 'I, I')) \
          .withColumn('Provider Name Suffix Text', regexp_replace('Provider Name Suffix Text', 'II', 'II, II')) \
          .withColumn('Provider Name Suffix Text', regexp_replace('Provider Name Suffix Text', 'III', 'III, III')) \
          .withColumn('Provider Name Suffix Text', regexp_replace('Provider Name Suffix Text', 'IV', 'IV, IV')) \
          .withColumn('Provider Name Suffix Text', regexp_replace('Provider Name Suffix Text', 'V', 'V, V')) \
          .withColumn('Provider Name Suffix Text', regexp_replace('Provider Name Suffix Text', 'VI', 'VI, VI')) \
          .withColumn('Provider Name Suffix Text', regexp_replace('Provider Name Suffix Text', 'VII', 'VII, VII')) \
          .withColumn('Provider Name Suffix Text', regexp_replace('Provider Name Suffix Text', 'VIII', 'VIII, VIII')) \
          .withColumn('Provider Name Suffix Text', regexp_replace('Provider Name Suffix Text', 'IX', 'IX, IX')) 
df13.show()        

+----------+----------------+---------------+------------------------------------+------------------------------------------------+-------------------------------+-------------------+--------------------+-------------------------+-------------------------+------------------------+--------------------------------+------------------------------------------+------------------------+-------------------------+--------------------------+-------------------------------+-------------------------------+------------------------------+----------------------------------+--------------------------------------------+---------------------------------------------+-------------------------------------------+--------------------------------------------+---------------------------------------------+----------------------------------------------------------------+--------------------------------------------------+--------------------------------------------+------------------------------------------------

In [ ]:
df14=df13.withColumn('Provider Other Name Suffix Text', regexp_replace('Provider Other Name Suffix Text', 'Jr.', 'Jr., Jr')) \
           .withColumn('Provider Other Name Suffix Text', regexp_replace('Provider Other Name Suffix Text', 'Sr.', 'Sr., Sr.'))\
           .withColumn('Provider Other Name Suffix Text', regexp_replace('Provider Other Name Suffix Text', 'I', 'I, I')) \
           .withColumn('Provider Other Name Suffix Text', regexp_replace('Provider Other Name Suffix Text', 'II', 'II, II')) \
           .withColumn('Provider Other Name Suffix Text', regexp_replace('Provider Other Name Suffix Text', 'III', 'III, III')) \
           .withColumn('Provider Other Name Suffix Text', regexp_replace('Provider Other Name Suffix Text', 'IV', 'IV, IV')) \
           .withColumn('Provider Other Name Suffix Text', regexp_replace('Provider Other Name Suffix Text', 'V', 'V, V')) \
           .withColumn('Provider Other Name Suffix Text', regexp_replace('Provider Other Name Suffix Text', 'VI', 'VI, VI')) \
           .withColumn('Provider Other Name Suffix Text', regexp_replace('Provider Other Name Suffix Text', 'VII', 'VII, VII')) \
           .withColumn('Provider Other Name Suffix Text', regexp_replace('Provider Other Name Suffix Text', 'VIII', 'VIII, VIII')) \
           .withColumn('Provider Other Name Suffix Text', regexp_replace('Provider Other Name Suffix Text', 'IX', 'IX, IX')) 
df14.show(100) 

+----------+----------------+---------------+------------------------------------+------------------------------------------------+-------------------------------+-------------------+--------------------+-------------------------+-------------------------+------------------------+--------------------------------+------------------------------------------+------------------------+-------------------------+--------------------------+-------------------------------+-------------------------------+------------------------------+----------------------------------+--------------------------------------------+---------------------------------------------+-------------------------------------------+--------------------------------------------+---------------------------------------------+----------------------------------------------------------------+--------------------------------------------------+--------------------------------------------+------------------------------------------------

State Codes

In [ ]:

df15=df14.withColumn('Provider Business Mailing Address State Name', regexp_replace('Provider Business Mailing Address State Name', 'FL', 'FL, FLORIDA, S')) \
           .withColumn('Provider Business Mailing Address State Name', regexp_replace('Provider Business Mailing Address State Name', 'IA', 'IA, IOWA, S')) \
           .withColumn('Provider Business Mailing Address State Name', regexp_replace('Provider Business Mailing Address State Name', 'ME', 'ME, MAINE, S')) \
           .withColumn('Provider Business Mailing Address State Name', regexp_replace('Provider Business Mailing Address State Name', 'UT', 'UT, UTAH, S')) \
           .withColumn('Provider Business Mailing Address State Name', regexp_replace('Provider Business Mailing Address State Name', 'WY', 'WY, WYOMING, S')) 
df15.show()

+----------+----------------+---------------+------------------------------------+------------------------------------------------+-------------------------------+-------------------+--------------------+-------------------------+-------------------------+------------------------+--------------------------------+------------------------------------------+------------------------+-------------------------+--------------------------+-------------------------------+-------------------------------+------------------------------+----------------------------------+--------------------------------------------+---------------------------------------------+-------------------------------------------+--------------------------------------------+---------------------------------------------+----------------------------------------------------------------+--------------------------------------------------+--------------------------------------------+------------------------------------------------

In [ ]:
df16=df15.withColumn('Provider Business Practice Location Address State Name', regexp_replace('Provider Business Practice Location Address state Name', 'MO,', 'MO, MISSOURI, S')) \
           .withColumn('Provider Business Practice Location Address State Name', regexp_replace('Provider Business Practice Location Address state Name', 'PW', 'PW, PALAU, T')) \
           .withColumn('Provider Business Practice Location Address State Name', regexp_replace('Provider Business Practice Location Address state Name', 'UT', 'UT, UTAH, S')) \
           .withColumn('Provider Business Practice Location Address State Name', regexp_replace('Provider Business Practice Location Address state Name', 'HI ', 'HI, HAWAII, S')) \
           .withColumn('Provider Business Practice Location Address State Name', regexp_replace('Provider Business Practice Location Address state Name', 'WY', 'WY, WYOMING, S')) 
df16.show()        

+----------+----------------+---------------+------------------------------------+------------------------------------------------+-------------------------------+-------------------+--------------------+-------------------------+-------------------------+------------------------+--------------------------------+------------------------------------------+------------------------+-------------------------+--------------------------+-------------------------------+-------------------------------+------------------------------+----------------------------------+--------------------------------------------+---------------------------------------------+-------------------------------------------+--------------------------------------------+---------------------------------------------+----------------------------------------------------------------+--------------------------------------------------+--------------------------------------------+------------------------------------------------

In [ ]:
df17=df16.withColumn('Other Provider Identifier State_1', regexp_replace('Other Provider Identifier State_1', 'FL', 'FL, FLORIDA, S')) \
           .withColumn('Other Provider Identifier State_1', regexp_replace('Other Provider Identifier State_1', 'IA', 'IA, IOWA, S')) \
           .withColumn('Other Provider Identifier State_1', regexp_replace('Other Provider Identifier State_1', 'ME', 'ME, MAINE, S')) \
           .withColumn('Other Provider Identifier State_1', regexp_replace('Other Provider Identifier State_1', 'UT', 'UT, UTAH, S')) \
           .withColumn('Other Provider Identifier State_1', regexp_replace('Other Provider Identifier State_1', 'WY', ' WY, WYOMING, S')) 
df17.show()     



+----------+----------------+---------------+------------------------------------+------------------------------------------------+-------------------------------+-------------------+--------------------+-------------------------+-------------------------+------------------------+--------------------------------+------------------------------------------+------------------------+-------------------------+--------------------------+-------------------------------+-------------------------------+------------------------------+----------------------------------+--------------------------------------------+---------------------------------------------+-------------------------------------------+--------------------------------------------+---------------------------------------------+----------------------------------------------------------------+--------------------------------------------------+--------------------------------------------+------------------------------------------------

In [ ]:
df17=df16.withColumn('Provider License Number State Code_1', regexp_replace('Provider License Number State Code_1', 'FL', 'FL, FLORIDA, S')) \
           .withColumn('Provider License Number State Code_1', regexp_replace('Provider License Number State Code_1', 'IA', 'IA, IOWA, S')) \
           .withColumn('Provider License Number State Code_1', regexp_replace('Provider License Number State Code_1', 'ME', 'ME, MAINE, S')) \
           .withColumn('Provider License Number State Code_1', regexp_replace('Provider License Number State Code_1', 'UT', 'UT, UTAH, S')) \
           .withColumn('Provider License Number State Code_1', regexp_replace('Provider License Number State Code_1', 'WY', 'WY, WYOMING, S')) 
df17.show()       

+----------+----------------+---------------+------------------------------------+------------------------------------------------+-------------------------------+-------------------+--------------------+-------------------------+-------------------------+------------------------+--------------------------------+------------------------------------------+------------------------+-------------------------+--------------------------+-------------------------------+-------------------------------+------------------------------+----------------------------------+--------------------------------------------+---------------------------------------------+-------------------------------------------+--------------------------------------------+---------------------------------------------+----------------------------------------------------------------+--------------------------------------------------+--------------------------------------------+------------------------------------------------

In [ ]:
# Primary Taxonomy Codes
df18=df17.withColumn( 'Healthcare Provider Primary Taxonomy Switch_1', regexp_replace( 'Healthcare Provider Primary Taxonomy Switch_1', 'X', 'X, Not Answered')) \
           .withColumn( 'Healthcare Provider Primary Taxonomy Switch_1', regexp_replace( 'Healthcare Provider Primary Taxonomy Switch_1', 'Y', 'Y, Yes')) \
           .withColumn( 'Healthcare Provider Primary Taxonomy Switch_1', regexp_replace( 'Healthcare Provider Primary Taxonomy Switch_1', 'N', 'N, No')) 
df18.show()          
 

+----------+----------------+---------------+------------------------------------+------------------------------------------------+-------------------------------+-------------------+--------------------+-------------------------+-------------------------+------------------------+--------------------------------+------------------------------------------+------------------------+-------------------------+--------------------------+-------------------------------+-------------------------------+------------------------------+----------------------------------+--------------------------------------------+---------------------------------------------+-------------------------------------------+--------------------------------------------+---------------------------------------------+----------------------------------------------------------------+--------------------------------------------------+--------------------------------------------+------------------------------------------------

writing final transformed file into *json*

In [ ]:
df18.write.csv("Users\final_jason1.jason",header=True)